# Explore here

In [2]:
import pandas as pd
import numpy as np

In [53]:
X_train = pd.read_csv('https://raw.githubusercontent.com/4GeeksAcademy/Finarosalina_Random_Forest_/main/data/processed/X_train2.csv')
y_train = pd.read_csv('https://raw.githubusercontent.com/4GeeksAcademy/Finarosalina_Random_Forest_/main/data/processed/y_train2.csv')
X_test = pd.read_csv('https://raw.githubusercontent.com/4GeeksAcademy/Finarosalina_Random_Forest_/main/data/processed/X_test2.csv')
y_test = pd.read_csv('https://raw.githubusercontent.com/4GeeksAcademy/Finarosalina_Random_Forest_/main/data/processed/y_test2.csv')

y_test

y_train = y_train.squeeze()
y_test = y_test.squeeze()
X_train


Pregnancies  Glucose  BloodPressure  Insulin   BMI  \
0              9      102             76        0  32.9   
1              6       87             80        0  23.2   
2              8       65             72        0  32.0   
3              0       86             68        0  35.8   
4             12       88             74       54  35.3   
..           ...      ...            ...      ...   ...   
508            4      123             80      176  32.0   
509            9      122             56        0  33.3   
510           13      152             90       29  26.8   
511            3      116             74      105  26.3   
512            1      118             58       94  33.3   

     DiabetesPedigreeFunction  Age  
0                       0.665   46  
1                       0.084   32  
2                       0.600   42  
3                       0.238   25  
4                       0.378   48  
..                        ...  ...  
508                     0.443   34  
509                     1.114   33  
510                     0.731   43  
511                     0.107   24  
512                     0.261   23  

[513 rows x 7 columns]

In [23]:
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.metrics import accuracy_score, classification_report

# Crear el modelo con boosting
model = GradientBoostingClassifier(n_estimators=17, random_state=42)

# Entrenar con los datos de entrenamiento
model.fit(X_train, y_train)

# Predecir sobre los datos de prueba
y_pred = model.predict(X_test)

# Evaluar
print("Accuracy:", accuracy_score(y_test, y_pred))
print(classification_report(y_test, y_pred))


Accuracy: 0.813953488372093
              precision    recall  f1-score   support

           0       0.83      0.92      0.87        90
           1       0.76      0.56      0.65        39

    accuracy                           0.81       129
   macro avg       0.79      0.74      0.76       129
weighted avg       0.81      0.81      0.81       129



In [55]:
from xgboost import XGBClassifier
from sklearn.metrics import accuracy_score, classification_report

# modelo con XGBoost
model = XGBClassifier(
    n_estimators=17,
    max_depth=3,
    learning_rate=0.1,
    use_label_encoder=False,
    eval_metric='logloss',
    random_state=42
)

# Entrenar
model.fit(X_train, y_train)

# Predecir
y_pred = model.predict(X_test)

# Evaluar
print("Accuracy:", accuracy_score(y_test, y_pred))
print(classification_report(y_test, y_pred))


Accuracy: 0.8062015503875969
              precision    recall  f1-score   support

           0       0.84      0.90      0.87        90
           1       0.72      0.59      0.65        39

    accuracy                           0.81       129
   macro avg       0.78      0.74      0.76       129
weighted avg       0.80      0.81      0.80       129



/home/vscode/.local/lib/python3.11/site-packages/xgboost/training.py:183: UserWarning: [18:19:14] WARNING: /workspace/src/learner.cc:738: 
Parameters: { "use_label_encoder" } are not used.

  bst.update(dtrain, iteration=i, fobj=obj)


In [ ]:
from sklearn.ensemble import AdaBoostClassifier
from sklearn.metrics import accuracy_score, classification_report

ada = AdaBoostClassifier(n_estimators=100, learning_rate=0.1, random_state=42)

ada.fit(X_train, y_train)

ada_y_pred_train = ada.predict(X_train)
ada_y_pred_test = ada.predict(X_test)

ada_accuracy_train = accuracy_score(y_train, ada_y_pred_train)
ada_accuracy_test = accuracy_score(y_test, ada_y_pred_test)

print(f"Accuracy (Train): {ada_accuracy_train}")
print(f"Accuracy (Test): {ada_accuracy_test}")

print("Classification Report (Test):")
print(classification_report(y_test, ada_y_pred_test, target_names=["No Diabético", "Diabético"]))





Accuracy (Train): 0.7816764132553606
Accuracy (Test): 0.8294573643410853
Classification Report (Test):
              precision    recall  f1-score   support

No Diabético       0.83      0.96      0.89        90
   Diabético       0.84      0.54      0.66        39

    accuracy                           0.83       129
   macro avg       0.83      0.75      0.77       129
weighted avg       0.83      0.83      0.82       129



In [59]:
from sklearn.metrics import classification_report

# Asegúrate de tener esto antes
y_pred_test = model.predict(X_test)

# Luego genera el reporte correctamente
print(classification_report(
    y_test,
    y_pred_test,
    target_names=["No Diabético", "Diabético"]
))


              precision    recall  f1-score   support

No Diabético       0.84      0.90      0.87        90
   Diabético       0.72      0.59      0.65        39

    accuracy                           0.81       129
   macro avg       0.78      0.74      0.76       129
weighted avg       0.80      0.81      0.80       129



pasa igual, no es muy bueno detectando los si por lo que voy a hacer un gridsearch

In [66]:
from sklearn.ensemble import AdaBoostClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.model_selection import GridSearchCV

base_tree = DecisionTreeClassifier(max_depth=1, random_state=42)

ada = AdaBoostClassifier(estimator=base_tree, random_state=42)

param_grid = {
    'n_estimators': [17, 50, 100, 200],
    'learning_rate': [0.01, 0.1, 1.0]
}

# Realizar GridSearchCV
grid_search = GridSearchCV(
    estimator=ada,
    param_grid=param_grid,
    scoring='recall',  # Cambiar a 'recall' para priorizar la detección de diabéticos
    cv=5,
    n_jobs=-1,  # Usar todos los núcleos disponibles
    refit='recall'  # Reajustar el mejor modelo según recall
)


grid_search.fit(X_train, y_train)


print("Mejores parámetros encontrados: ", grid_search.best_params_)
print("Mejor puntuación (Recall): ", grid_search.best_score_)

print("Resultados para cada combinación de parámetros:")
print(grid_search.cv_results_)


Mejores parámetros encontrados:  {'learning_rate': 1.0, 'n_estimators': 200}
Mejor puntuación (Recall):  0.5764705882352941
Resultados para cada combinación de parámetros:
{'mean_fit_time': array([0.04023271, 0.11022692, 0.2567903 , 0.46322846, 0.04497738,
       0.13174834, 0.21430936, 0.47120724, 0.04463859, 0.10967884,
       0.21865363, 0.44887781]), 'std_fit_time': array([0.00114459, 0.00173021, 0.02581607, 0.02503162, 0.01002168,
       0.0207923 , 0.00128967, 0.04684719, 0.006082  , 0.00241676,
       0.00440345, 0.06803307]), 'mean_score_time': array([0.00878859, 0.01546774, 0.03241053, 0.05637212, 0.01020241,
       0.0160543 , 0.02708569, 0.05858526, 0.00920172, 0.0151392 ,
       0.02699342, 0.04877062]), 'std_score_time': array([0.00124521, 0.00042218, 0.01008612, 0.01527573, 0.00292209,
       0.00227008, 0.00117764, 0.01981716, 0.00281326, 0.00020812,
       0.0016163 , 0.01419644]), 'param_learning_rate': masked_array(data=[0.01, 0.01, 0.01, 0.01, 0.1, 0.1, 0.1, 0.1, 1.0

In [70]:

ada_best = AdaBoostClassifier(learning_rate=1.0, n_estimators=200, random_state=42)


ada_best.fit(X_train, y_train)

y_pred_train_best = ada_best.predict(X_train)
y_pred_test_best = ada_best.predict(X_test)


accuracy_train_best = accuracy_score(y_train, y_pred_train_best)
accuracy_test_best = accuracy_score(y_test, y_pred_test_best)


print(f"Accuracy (Train) con los mejores parámetros: {accuracy_train_best}")
print(f"Accuracy (Test) con los mejores parámetros: {accuracy_test_best}")

print("Classification Report (Test) con los mejores parámetros:")
print(classification_report(y_test, y_pred_test_best, target_names=["No Diabético", "Diabético"]))


Accuracy (Train) con los mejores parámetros: 0.8187134502923976
Accuracy (Test) con los mejores parámetros: 0.7751937984496124
Classification Report (Test) con los mejores parámetros:
              precision    recall  f1-score   support

No Diabético       0.82      0.87      0.84        90
   Diabético       0.65      0.56      0.60        39

    accuracy                           0.78       129
   macro avg       0.73      0.72      0.72       129
weighted avg       0.77      0.78      0.77       129



In [ ]:
from lightgbm import LGBMClassifier
from sklearn.metrics import accuracy_score, classification_report


lgb = LGBMClassifier(n_estimators=100, learning_rate=0.1, random_state=42)

lgb.fit(X_train, y_train)

y_pred_train_lgb = lgb.predict(X_train)
y_pred_test_lgb = lgb.predict(X_test)

accuracy_train_lgb = accuracy_score(y_train, y_pred_train_lgb)
accuracy_test_lgb = accuracy_score(y_test, y_pred_test_lgb)

print(f"Accuracy (Train) con LGBMClassifier: {accuracy_train_lgb}")
print(f"Accuracy (Test) con LGBMClassifier: {accuracy_test_lgb}")

print("Classification Report (Test) con LGBMClassifier:")
print(classification_report(y_test, y_pred_test_lgb, target_names=["No Diabético", "Diabético"]))


[LightGBM] [Info] Number of positive: 170, number of negative: 343
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000075 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 540
[LightGBM] [Info] Number of data points in the train set: 513, number of used features: 7
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.331384 -> initscore=-0.701932
[LightGBM] [Info] Start training from score -0.701932
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best 

Accuracy (Train) con LGBMClassifier: 1.0
Accuracy (Test) con LGBMClassifier: 0.7286821705426356
Classification Report (Test) con LGBMClassifier:
              precision    recall  f1-score   support

No Diabético       0.82      0.79      0.80        90
   Diabético       0.55      0.59      0.57        39

    accuracy                           0.73       129
   macro avg       0.68      0.69      0.69       129
weighted avg       0.73      0.73      0.73       129


In [ ]:
from lightgbm import LGBMClassifier
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import accuracy_score, classification_report

lgb = LGBMClassifier(random_state=42)


param_grid = {
    'n_estimators': [50, 100, 200],
    'learning_rate': [0.01, 0.1, 0.2],
    'max_depth': [3, 5, 7],  
    'num_leaves': [31, 50, 70]  
}


grid_search = GridSearchCV(
    estimator=lgb,
    param_grid=param_grid,
    scoring='recall',  # 'recall'para  mejorar la capacidad de predecir la enfermedad (valores asimetricos de predicción)
    cv=5,  
    n_jobs=-1,  
    verbose=1  
)

grid_search.fit(X_train, y_train)

print("Mejores parámetros encontrados: ", grid_search.best_params_)

y_pred_train_lgb = grid_search.best_estimator_.predict(X_train)
y_pred_test_lgb = grid_search.best_estimator_.predict(X_test)

accuracy_train_lgb = accuracy_score(y_train, y_pred_train_lgb)
accuracy_test_lgb = accuracy_score(y_test, y_pred_test_lgb)

print(f"Accuracy (Train) con LGBMClassifier: {accuracy_train_lgb}")
print(f"Accuracy (Test) con LGBMClassifier: {accuracy_test_lgb}")

print("Classification Report (Test) con LGBMClassifier:")
print(classification_report(y_test, y_pred_test_lgb, target_names=["No Diabético", "Diabético"]))


Fitting 5 folds for each of 81 candidates, totalling 405 fits
[LightGBM] [Info] Number of positive: 136, number of negative: 274
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000063 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 463
[LightGBM] [Info] Number of data points in the train set: 410, number of used features: 7
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.331707 -> initscore=-0.700473
[LightGBM] [Info] Start training from score -0.700473
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[L

se aprecia overfitting, Accuracy en entrenamiento: 98.4% / Accuracy en prueba: 72.9% ❗️

In [ ]:
from lightgbm import LGBMClassifier

model = LGBMClassifier(
    learning_rate=0.2,
    max_depth=5,
    n_estimators=50,
    num_leaves=31,
    is_unbalance=True  
)


In [ ]:
from lightgbm import LGBMClassifier
from sklearn.model_selection import GridSearchCV

# Modelo base con is_unbalance activado para tratar de compesar los datos
lgb = LGBMClassifier(
    random_state=42,
    is_unbalance=True
)


param_grid = {
    'n_estimators': [50, 100],
    'learning_rate': [0.05, 0.1],
    'max_depth': [3, 4],
    'num_leaves': [15, 31],
    'reg_alpha': [0, 0.1, 1],   
    'reg_lambda': [0, 0.1, 1]   
}

# Búsqueda con enfoque en el recall (para detectar diabéticos)
grid_search = GridSearchCV(
    estimator=lgb,
    param_grid=param_grid,
    scoring='recall',
    cv=5,
    n_jobs=-1,
    verbose=1
)

grid_search.fit(X_train, y_train)

print("Mejores parámetros encontrados: ", grid_search.best_params_)

from sklearn.metrics import accuracy_score, classification_report

y_pred_test = grid_search.best_estimator_.predict(X_test)
y_pred_train = grid_search.best_estimator_.predict(X_train)

print("Accuracy (Train):", accuracy_score(y_train, y_pred_train))
print("Accuracy (Test):", accuracy_score(y_test, y_pred_test))
print("Classification Report (Test):")
print(classification_report(y_test, y_pred_test, target_names=["No Diabético", "Diabético"]))


Métrica	                Entrenamiento	Test	Diferencia
Accuracy	            83.04%	        72.09%	~11%
Recall (Diabético)      64%	            64%	Igual (mejoró respecto a antes)
F1-score (Diabético)	58%	            58%	Igual

In [78]:
from sklearn.ensemble import GradientBoostingClassifier, AdaBoostClassifier
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier

gb_model = GradientBoostingClassifier(n_estimators=17, random_state=42)
gb_model.fit(X_train, y_train)


xgb_model = XGBClassifier(
    n_estimators=17,
    max_depth=3,
    learning_rate=0.1,
    use_label_encoder=False,
    eval_metric='logloss',
    random_state=42
)
xgb_model.fit(X_train, y_train)

ada_model = AdaBoostClassifier(n_estimators=100, learning_rate=0.1, random_state=42)
ada_model.fit(X_train, y_train)

# AdaBoostClassifier (mejorado)
ada_best_model = AdaBoostClassifier(learning_rate=1.0, n_estimators=200, random_state=42)
ada_best_model.fit(X_train, y_train)

lgb_model = LGBMClassifier(n_estimators=100, learning_rate=0.1, random_state=42)
lgb_model.fit(X_train, y_train)


/home/vscode/.local/lib/python3.11/site-packages/xgboost/training.py:183: UserWarning: [19:18:22] WARNING: /workspace/src/learner.cc:738: 
Parameters: { "use_label_encoder" } are not used.

  bst.update(dtrain, iteration=i, fobj=obj)


[LightGBM] [Info] Number of positive: 170, number of negative: 343
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000056 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 540
[LightGBM] [Info] Number of data points in the train set: 513, number of used features: 7
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.331384 -> initscore=-0.701932
[LightGBM] [Info] Start training from score -0.701932
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best 

LGBMClassifier(random_state=42)

In [79]:
import joblib

gb_model_path = '/workspaces/Finarosalina_BOOSTING_ML_python_template/models/gb_model.joblib'
xgb_model_path = '/workspaces/Finarosalina_BOOSTING_ML_python_template/models/xgb_model.joblib'
ada_model_path = '/workspaces/Finarosalina_BOOSTING_ML_python_template/models/ada_model.joblib'
ada_best_model_path = '/workspaces/Finarosalina_BOOSTING_ML_python_template/models/ada_best_model.joblib'
lgb_model_path = '/workspaces/Finarosalina_BOOSTING_ML_python_template/models/lgb_model.joblib'

joblib.dump(gb_model, gb_model_path)
joblib.dump(xgb_model, xgb_model_path)
joblib.dump(ada_model, ada_model_path)
joblib.dump(ada_best_model, ada_best_model_path)
joblib.dump(lgb_model, lgb_model_path)



['/workspaces/Finarosalina_BOOSTING_ML_python_template/models/lgb_model.joblib']

In [82]:
X_train.to_csv('/workspaces/Finarosalina_BOOSTING_ML_python_template/data/processed/X_train.csv', index=False)
y_train.to_csv('/workspaces/Finarosalina_BOOSTING_ML_python_template/data/processed/y_train.csv', index=False)
X_test.to_csv('/workspaces/Finarosalina_BOOSTING_ML_python_template/data/processed/X_test.csv', index=False)
y_test.to_csv('/workspaces/Finarosalina_BOOSTING_ML_python_template/data/processed/y_test.csv', index=False)

In [83]:
import json

with open('/workspaces/Finarosalina_BOOSTING_ML_python_template/src/explore.ipynb', 'r') as f:
    notebook_content = json.load(f)


code_cells = [cell['source'] for cell in notebook_content['cells'] if cell['cell_type'] == 'code']


code = '\n'.join([''.join(cell) for cell in code_cells])


with open('/workspaces/Finarosalina_BOOSTING_ML_python_template/src/app.py', 'w') as f:
    f.write(code)
